In [1]:
import os
import time

import pandas as pd
from probabilistic_model.learning.jpt.jpt import JPT
from probabilistic_model.learning.jpt.variables import infer_variables_from_dataframe
from random_events.events import Event
from random_events.variables import Continuous

from pycram.costmaps import OccupancyCostmap
from pycram.plan_failures import PlanFailure
from pycram.designators.object_designator import ObjectDesignatorDescription
from pycram.bullet_world import BulletWorld, Object
from pycram.robot_descriptions import robot_description
from pycram.enums import ObjectType, Arms, Grasp
from pycram.pose import Pose
from pycram.ros.viz_marker_publisher import VizMarkerPublisher
from pycram.process_module import ProcessModule
import sqlalchemy

from pycram.resolver.location.jpt_location import FunkyPickUpAction
from pycram.process_module import simulated_robot

import plotly.graph_objects as go

Unknown attribute "type" in /robot[@name='pr2']/link[@name='base_laser_link']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='wide_stereo_optical_frame']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='narrow_stereo_optical_frame']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='laser_tilt_link']
[WARN] [1710260140.694276]: Could not import RoboKudo messages, RoboKudo interface could not be initialized


In [2]:
pycrorm_uri = os.getenv('PYCRORM_URI')
pycrorm_uri = "mysql+pymysql://" + pycrorm_uri

In [3]:
world = BulletWorld("DIRECT")
robot = Object(robot_description.name, ObjectType.ROBOT, robot_description.name + ".urdf")
milk = Object("milk", ObjectType.MILK, "milk.stl", pose=Pose([1.3, 1, 0.9]))
viz_marker_publisher = VizMarkerPublisher()
ProcessModule.execution_delay = False
engine = sqlalchemy.create_engine(pycrorm_uri)

Unknown tag "material" in /robot[@name='plane']/link[@name='planeLink']/collision[1]
Unknown tag "contact" in /robot[@name='plane']/link[@name='planeLink']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='base_laser_link']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='wide_stereo_optical_frame']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='narrow_stereo_optical_frame']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='laser_tilt_link']
Unknown tag "material" in /robot[@name='plane']/link[@name='planeLink']/collision[1]
Unknown tag "contact" in /robot[@name='plane']/link[@name='planeLink']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='base_laser_link']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='wide_stereo_optical_frame']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='narrow_stereo_optical_frame']
Unknown attribute "type" in /robot[@name='pr2']/link[@name='laser_tilt_link']


In [4]:
milk_description = ObjectDesignatorDescription(types=[ObjectType.MILK]).ground()
fpa = FunkyPickUpAction(milk_description, arms=[Arms.LEFT.value, Arms.RIGHT.value, Arms.BOTH.value], grasps=[Grasp.FRONT.value, Grasp.LEFT.value, Grasp.RIGHT.value, Grasp.TOP.value])
relative_x = Continuous("relative_x")
relative_y = Continuous("relative_y")
p_xy = fpa.policy.marginal([relative_x, relative_y])
fig = go.Figure(p_xy.root.plot(), p_xy.root.plotly_layout())
fig.show()


samples = pd.read_sql_query(fpa.query_for_database(), engine)
samples = samples.rename(columns={"anon_1": "relative_x", "anon_2": "relative_y"})

variables = infer_variables_from_dataframe(samples, scale_continuous_types=False)
model = JPT(variables, min_samples_leaf=0.05)
model.fit(samples)
model = model.probabilistic_circuit
arm, grasp, relative_x, relative_y = model.variables

In [5]:
event = Event({arm:"left", grasp:"front"})
conditional_model, conditional_probability = model.conditional(event)
conditional_probability

0.16896551724137923

In [6]:
p_xy = conditional_model.marginal([relative_x, relative_y])
fig = go.Figure(p_xy.root.plot_2d(), p_xy.root.plotly_layout())
fig.show()

In [7]:
# fpa.policy = model
# fpa.sample_amount = 500
# with simulated_robot:
#     fpa.try_out_policy()

In [8]:
modes, likelihood = model.mode()
mode = modes[0]
mode_model, _ = model.conditional(mode)
mode_xy = mode_model.marginal([relative_x, relative_y])
fig = go.Figure(mode_xy.root.plot_2d(), mode_xy.root.plotly_layout())
fig.show()

In [9]:
# fpa.policy = mode_model
# fpa.sample_amount = 500
# with simulated_robot:
#     fpa.try_out_policy()

In [10]:
kitchen = Object("kitchen", ObjectType.ENVIRONMENT, "apartment.urdf")
milk.set_pose(Pose([0.5, 3.15, 1.04]))
model.root.update_variables({relative_x: relative_y, relative_y: relative_x})

# milk.set_pose(Pose([3.2, 3.15, 1.04], [0, 0, 1, 1]))

Unknown tag "material" in /robot[@name='apartment']/link[@name='coffe_machine']/collision[1]
Unknown tag "material" in /robot[@name='apartment']/link[@name='coffe_machine']/collision[1]


In [11]:
milk_description = ObjectDesignatorDescription(types=[ObjectType.MILK]).ground()
fpa = FunkyPickUpAction(milk_description, arms=[Arms.LEFT.value, Arms.RIGHT.value, Arms.BOTH.value], grasps=[Grasp.FRONT.value, Grasp.LEFT.value, Grasp.RIGHT.value, Grasp.TOP.value], policy=model)
fpa.sample_amount = 200

In [12]:
grounded_model = fpa.ground_model(fpa.policy, fpa.events_from_occupancy_costmap())
p_xy = grounded_model.marginal([relative_x, relative_y])
fig = go.Figure(p_xy.root.plot_2d(), p_xy.root.plotly_layout())
fig.update_xaxes(range=[-1, 1])
fig.update_yaxes(range=[-1, 1])
fig.show()

In [13]:
with simulated_robot:
    for sample in fpa:
        try:
            sample.perform()
            break
        except PlanFailure as e:
            print(type(e))
            time.sleep(1)
            continue

navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>
navigate works
facing works
<class 'pycram.plan_failures.IKError'>


KeyboardInterrupt: 

In [ ]:
# world.exit()
# viz_marker_publisher._stop_publishing()